![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 15. <i>Korekta gramatyczna</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Ostatnią z omawianych przez nas technik stosowaną podczas wspomagania tłumaczenia jest korekta gramatyczna. Automatyczna korekta gramatyczna tekstu to ambitne zadanie odnalezienia możliwych błędów niezwiązanych bezpośrednio z pisownią. Są to między innymi:
* błędy gramatyczne
* źle użyte słowa
* złe połączenia wyrazowe
* błędy interpunkcyjne
* kolokwializmy
* redundancja (np. "tylko i wyłącznie")

Warto zwrócić uwagę, iż systemy do korekcji gramatycznej można traktować jako klasyfikatory binarne. Przyjmijmy, że odpowiedź pozytywna korektora to wykrycie błędu w tekście, natomiast negatywna - brak błędu. Wówczas rozróżniamy dwa typy pomyłek: false positive oraz false negative. False positive to tzw. "fałszywy alarm" - zbyt duża ich ilość spowoduje wydłużenie czasu pracy użytkownika przez konieczność analizowania zgłoszeń, które w istocie błędami nie są. Co jednak jeszcze gorsze, zbyt duża ilość false positives powoduje spadek zaufania użytkownika do systemu oraz drastyczny spadek satysfakcji z używania systemu. Te drugie błędy - false negatives - to z kolei faktyczne błędy w tekście, które nie zostały wyłapane przez system korekty. Stare polskie porzekadło głosi, że "czego oko nie widzi, tego sercu nie żal". Niestety jednak problem pojawia się, kiedy dostrzeże to jakieś inne oko... Wysoka liczba false negatives wprawdzie skraca czas korekty (sic!), ale odbywa się to kosztem jakości całego procesu. Idealnie zatem byłoby zminimalizować zarówno liczbę false positives, jak i false negatives. Jak jednak łatwo się domyślić, nie jest to zawsze możliwe. Korektor gramatyczny, który jest bardzo restrykcyjny i raportuje wiele błędów, będzie miał tendencję do popełniania false positives. Natomiast korektor bardziej pobłażliwy niechybnie popełni wiele false negatives. Co zatem jest ważniejsze? Praktyka wskazuje, że oba parametry mają podobną wagę, ale jednak odrobinę ważniejsze jest powstrzymanie się od false positives.

Do najbardziej popularnych narzędzi wspomagających korektę gramatyczną tekstu należą Grammarly oraz LanguageTool. Na dzisiejszych zajęciach zajmiemy się tym drugim. LanguageTool został pierwotnie napisany jako praca dyplomowa Daniela Nabera, a następnie intensywnie rozwijany wspólnie z Marcinem Miłkowskim. Aż do dziś projekt jest ciągle rozwijany, zwiększana jest liczba obsługiwanych języków oraz dokładność działania.

LanguageTool jest systemem opartym na regułach. W dobie wszechobecnej sztucznej inteligencji opartej na uczeniu maszynowym rozwiązanie to wydaje się nieco przestarzałe. Jednak to właśnie reguły stanowią o sile LanguageToola - pozwalają one na zwiększenie precyzji korektora poprzez minimalizację false positives. Warto wspomnieć, iż liczne reguły LanguageToola dotyczą również korekty pisowni. Czyni to z LanguageToola kompletne narzędzie do korekty tekstu. Polecam przejrzenie zestawu reguł LanguageToola dla języka angielskiego: https://community.languagetool.org/rule/list?lang=en

Czas uruchomić to narzędzie. Skorzystajmy z Pythona.

In [1]:
!pip install language_tool_python

Następnie możemy użyć LanguageToola w programie Pythonowym: (przykład zaczerpnięty z oficjalnego tutoriala: https://pypi.org/project/language-tool-python/)

In [2]:
import language_tool_python
import pprint
tool = language_tool_python.LanguageTool('en-US') 

text = 'A sentence with a error in the Hitchhiker’s Guide tot he Galaxy'

pp = pprint.PrettyPrinter(depth=2)
errors = tool.check(text)
pp.pprint(errors)

Unzipping /tmp/tmp2yjlywpj.zip to /home/potato/.cache/language_tool_python.
Downloaded https://www.languagetool.org/download/LanguageTool-6.4.zip to /home/potato/.cache/language_tool_python.


[Match({'ruleId': 'EN_A_VS_AN', 'message': 'Use “an” instead of ‘a’ if the following word starts with a vowel sound, e.g. ‘an article’, ‘an hour’.', 'replacements': ['an'], 'offsetInContext': 16, 'context': 'A sentence with a error in the Hitchhiker’s Guide tot he ...', 'offset': 16, 'errorLength': 1, 'category': 'MISC', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"}),
 Match({'ruleId': 'TOT_HE', 'message': 'Did you mean “to the”?', 'replacements': ['to the'], 'offsetInContext': 43, 'context': '... with a error in the Hitchhiker’s Guide tot he Galaxy', 'offset': 50, 'errorLength': 6, 'category': 'TYPOS', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"})]


Przeanalizujmy format zwracanego wyniku. Otrzymujemy listę obiektów Match - zawiadomień o potencjalnym błędzie. Razem z każdym błędem otrzymujemy m.in. identyfikator użytej reguły, opis błędu, rekomendancję poprawy, kontekst.

### Ćwiczenie 1: Użyj LanguageTool do znalezienia jak największej liczby prawdziwych błędów na swoim ulubionym portalu internetowym. Skorzystaj z poznanych wcześniej technik web scrapingu. Uwaga - LanguageTool najprawdopodobniej oznaczy nazwy własne jako literówki - ten typ błędu nie powinien być brany pod uwagę.

In [3]:
import re
import requests
from bs4 import BeautifulSoup
import language_tool_python
import pprint


def fetch_page_content(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.content, 'html.parser')

    for unwanted in soup(["script", "style"]):
        unwanted.decompose()

    page_text = soup.get_text()

    clean_text = re.sub(r"\s+", " ", page_text)
    return clean_text


def identify_language_errors(site_url):
    issues = []
    page_content = fetch_page_content(site_url)
    language_tool = language_tool_python.LanguageTool('en-NZ')
    matches = language_tool.check(page_content)
    for match in matches:
        if match.ruleId != 'MORFOLOGIK_RULE_EN_US':
            issues.append(match)

    pprint.pprint(issues)
    return issues

identify_language_errors('https://www.mountainjade.co.nz/pages/greenstone-meanings-and-designs/toki-adze')


[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "półkolonieróżne"?', 'replacements': ['półkolonieróżne'], 'offsetInContext': 43, 'context': '...dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty po...', 'offset': 316, 'errorLength': 15, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': '- Sky Blue Education Blog Półkolonie Kontakt O nas Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty podczas półkolonii Sky Blue?'}),
 Match({'ruleId': 'UPPERCASE_SENTENCE_START', 'message': 'To zdanie nie zaczyna się wielką literą', 'replacements': ['Zobacz'], 'offsetInContext': 43, 'context': '... warsztaty podczas półkolonii Sky Blue? zobacz także: Jak sk

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "półkolonieróżne"?', 'replacements': ['półkolonieróżne'], 'offsetInContext': 43, 'context': '...dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty po...', 'offset': 316, 'errorLength': 15, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': '- Sky Blue Education Blog Półkolonie Kontakt O nas Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty podczas półkolonii Sky Blue?'}),
 Match({'ruleId': 'UPPERCASE_SENTENCE_START', 'message': 'To zdanie nie zaczyna się wielką literą', 'replacements': ['Zobacz'], 'offsetInContext': 43, 'context': '... warsztaty podczas półkolonii Sky Blue? zobacz także: Jak sk

### Ćwiczenie 2: Napisz skrypt, który poszuka błędów w komentarzach klasy Javowej (zwykłych // oraz w javadocach). Uruchom ten skrypt na źródłach wybranego opensourcowego projektu w Javie.

In [3]:
def correct_java_grammar(java_file_path):
    return []